In [1]:
import sys
sys.path.append('/app/')  # noqa

from jina import Document, DocumentArray, Flow, Executor, requests
from pathlib import Path
import numpy as np
import pandas as pd
from tqdm.auto import tqdm
import argparse
from memlish.executors.cache import RealSBERTEncoderCache
from memlish.executors.index import FaissIndexer
import torch
import hashlib

def my_hash(s): 
    return str(int(hashlib.md5(str(s).encode('utf-8')).hexdigest(), 16))

In [2]:
torch.multiprocessing.set_start_method('spawn', force=True) 

In [3]:
OUT_DIR = Path("/data/imgflip/v1/")
OUT_TEMPLATE_TEXTS_CSV = OUT_DIR/"template_texts.csv"

In [4]:
JINA_SBERT_EMBEDDING_TEMPLATE_TEXT_COLLECTION = "02_v1_images_sbert_all_mpnet_base_v2_imgflip_template_100k_embeddings"
MONGO_EMBEDDING_DB_NAME = 'memlish_db'

In [5]:
def text_input_docs(df):    
    for idx, row in df.iterrows():
        template_name = row["template_img_name"]
        try:
            template_text = row["text"]
            document_id = f"{template_name}_{my_hash(template_text)}"
            doc = Document(id=document_id, text=template_text)# tags={'filename': str(template_img_path)})
        except Exception as e:
            print(document_id)
            print(template_text)
            print(str(e))
        
        yield doc 

In [6]:
templates_df = pd.read_csv(OUT_TEMPLATE_TEXTS_CSV)

In [7]:
templates_df = templates_df[~templates_df['text'].isna()]

In [8]:
templates_df = templates_df[~templates_df.duplicated(["text", "template_img_name"])]

In [9]:
templates_df.head(2)

Unnamed: 0                                               text  \
0           0  WHERE IS THE CHOCKY MILK; THAT I SAVED LAST NI...   
1           1  POV: YOU SAID POST OR VOID INSTEAD OF POINT OF...   

                                                 alt  views  upvotes  \
0  Chainsaw Bear |  WHERE IS THE CHOCKY MILK; THA...     72        3   
1  Run |  POV: YOU SAID POST OR VOID INSTEAD OF P...     69        2   

   comments  template_name  template_img_name  
0         2  Chainsaw-Bear  Chainsaw-Bear.jpg  
1         0  Chainsaw-Bear  Chainsaw-Bear.jpg

In [10]:
k_to_take = 100
groups = []

for _, group in templates_df.groupby(['template_img_name']):
    selected_sorted = group.sort_values(by=['views'], ascending=False)[:k_to_take]
    groups.append(selected_sorted)

In [11]:
df = pd.concat(groups).reset_index(drop=True)
df.head(2)

Unnamed: 0                                               text  \
0      221950  I WON $10,000,000 IN THE LOTTERY AND DECIDED T...   
1      228696                I NEED TO REFILL MY CHILD REPELLENT   

                                                 alt   views  upvotes  \
0  10 Guy |  I WON $10,000,000 IN THE LOTTERY AND...  733523      305   
1  10 Guy | I NEED TO REFILL MY CHILD REPELLENT |...  684545       12   

   comments template_name template_img_name  
0       107        10-Guy        10-Guy.jpg  
1         0        10-Guy        10-Guy.jpg

In [12]:
embedder_params = {
        "device": 'cpu'
}

cache_params = {
    "embedder_params": embedder_params,
    "db_name": MONGO_EMBEDDING_DB_NAME, 
    "collection_name": JINA_SBERT_EMBEDDING_TEMPLATE_TEXT_COLLECTION,
    "embedding_field_name":'emb',
    "megabatch_size":8192
}

In [13]:
flow_text_encode = Flow().add(uses=RealSBERTEncoderCache, name="SBERT_encoder", uses_with=cache_params)
flow_text_encode

In [14]:
with flow_text_encode:
    flow_text_encode.post(on='', inputs=text_input_docs(df), request_size=10, show_progress=True)

⠸ 0/2 waiting SBERT_encoder gateway to be ready...                                

⠧ 1/2 waiting SBERT_encoder to be ready...                                        

⠴ 1/2 waiting SBERT_encoder to be ready...                                        

⠋ 1/2 waiting SBERT_encoder to be ready...                                        

Downloading: 100%|██████████| 1.18k/1.18k [00:00<00:00, 999kB/s]


...

100%|██████████| 1/1 [00:00<00:00,  7.45it/s]


⠸ Working... ━━━━━━━━━━━━━━━╸━━━━━━━━━━━━━━━━━━━━━━━━━ 1:40:54  1.1 step/s 

  0%|          | 0/1 [00:00<?, ?it/s]

⠼ Working... ━━━━━━━━━━━━━━━╸━━━━━━━━━━━━━━━━━━━━━━━━━ 1:40:54  1.1 step/s {'es_tag': 'TIMELOG', 'timestamp': '2022-11-01 18:38:35.461432', 'function': 'memlish.executors.bert.get_embeddings', 'duration': 0.333742618560791}
⠦       DONE ━━━━━━━━━━━━━━━━╸━━━━━━━━━━━━━━━━━━━━━━━━ 1:40:55  1.1 step/s 6656 steps done in 1 hour and 40 minutes and 55 seconds


100%|██████████| 1/1 [00:00<00:00,  2.98it/s]
